In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import json
from itertools import islice

import pandas as pd

_df = pd.read_csv("/data/medivh_data/las.sample.part-1.meta.v2.tsv", sep="\t")
file_name_source_map = _df.set_index("file")["source"].fillna("").to_dict()

In [3]:
# Train Resume
with open("/data/medivh_data/workv2_sample.tagged.fixed.jsonl") as f:
    data = [json.loads(line) for line in islice(f, 10000)]

source_data = {}
for i in data:
    source = file_name_source_map.get(i["file"], "")
    if source:
        if source not in source_data:
            source_data[source] = []
        if len(source_data[source]) <= 500:
            source_data[source].append(i)

source_data["UNK"] = []
for i in data:
    source = file_name_source_map.get(i["file"], "")
    if source == "":
        source_data["UNK"].append(i)
source_data["UNK"] = source_data["UNK"][:1200]
train_resume = []
for k, v in source_data.items():
    train_resume.extend(v)

In [6]:
# Valid Resume
with open("/data/medivh_data/workv2_sample.tagged.fixed.jsonl") as f:
    data = [json.loads(line) for line in islice(f, 10000, 10000+5000)]

source_data = {}
for i in data:
    source = file_name_source_map.get(i["file"], "")
    if source:
        if source not in source_data:
            source_data[source] = []
        if len(source_data[source]) <= 100:
            source_data[source].append(i)

source_data["UNK"] = []
for i in data:
    source = file_name_source_map.get(i["file"], "")
    if source == "":
        source_data["UNK"].append(i)
source_data["UNK"] = source_data["UNK"][:300]
valid_resume = []
for k, v in source_data.items():
    valid_resume.extend(v)

In [5]:
with open("data/train.jsonl", "w") as f:
    for record in train_resume:
        f.write(json.dumps(record)+"\n")

In [8]:
with open("data/valid.jsonl", "w") as f:
    for record in valid_resume:
        f.write(json.dumps(record)+"\n")

In [3]:
from latain.core import Block
from latain.data import BlockHandcraftRecord
from latain.feature import get_compare_features
from tqdm import tqdm

In [7]:
data = {"file": "0003cb47-c526-4705-8ceb-d4214afa2451.html-zh-cn", "objs": [[{"pos": [86.87767791748047, 668.3373620865193, 97.3926773071289, 683.8941095230427], "fsize": 10.513161659240723, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 2, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [105.282470703125, 668.3373620865193, 145.37660217285156, 683.8941095230427], "fsize": 10.513161659240723, "font": "NotoSansCJKsc-Bold", "color": [0, 0, 0], "bidx": 2, "page": 1, "text": [["\u5de5", "<KEYW>,<CJK>"], ["\u4f5c", "<KEYW>,<CJK>"], ["\u7ecf", "<KEYW>,<CJK>"], ["\u5386", "<KEYW>,<CJK>"]], "tags": ["O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [90.82156372070312, 699.2203119156209, 131.38987731933594, 714.7770593521443], "fsize": 10.513161659240723, "font": "NotoSansCJKsc-Bold", "color": [0, 0, 0], "bidx": 3, "page": 1, "text": [["2017", "<NUM>,<TMR>,<TMS>"], ["/", "<POS>,<TMR>"], ["5", "<TMR>,<NUM>"], ["-", "<POS>,<TMR>"]], "tags": ["B-timeRange", "I-timeRange", "I-timeRange", "I-timeRange"], "cats": "Work,Work"}, {"pos": [141.4347381591797, 699.2203119156209, 403.86997985839844, 714.7770593521443], "fsize": 10.513161659240723, "font": "NotoSansCJKsc-Bold", "color": [0, 0, 0], "bidx": 3, "page": 1, "text": [["\u81f3", "<CJK>,<TMR>"], ["\u4eca", "<CJK>,<TMR>"], [":", "<POS>"], ["\u4e0a", "<CJK>,<COM>"], ["\u6d77", "<CJK>,<COM>"], ["\u65b0", "<CJK>,<COM>"], ["\u70ac", "<CJK>,<COM>"], ["\u7f51", "<CJK>,<COM>"], ["\u7edc", "<CJK>,<COM>"], ["\u6709", "<KEYW>,<CJK>"], ["\u9650", "<KEYW>,<CJK>"], ["\u516c", "<KEYW>,<CJK>"], ["\u53f8", "<KEYW>,<CJK>"], ["\u5e7f", "<CJK>,<TIL>"], ["\u5dde", "<CJK>,<TIL>"], ["\u5206", "<CJK>,<TIL>"], ["\u516c", "<CJK>,<TIL>"], ["\u53f8", "<CJK>,<TIL>"], ["|", "<POS>"], ["MySQLDBA", "<ENG>,<TIL>"]], "tags": ["I-timeRange", "I-timeRange", "O", "B-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "O", "B-title"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 728.348516261324, 114.47747039794922, 741.9523675796834], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 728.348516261324, 197.29904174804688, 741.9523675796834], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u6240", "<CJK>,<TIL>"], ["\u5c5e", "<CJK>,<TIL>"], ["\u884c", "<CJK>,<TIL>"], ["\u4e1a", "<CJK>,<TIL>"], [":", "<POS>"], ["\u4e92", "<CJK>"], ["\u8054", "<CJK>"], ["\u7f51", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 746.0897882339802, 114.47747039794922, 759.6936395523396], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 746.0897882339802, 212.09017944335938, 759.6936395523396], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u5de5", "<KEYW>,<CJK>"], ["\u4f5c", "<KEYW>,<CJK>"], ["\u5c97", "<KEYW>,<CJK>"], ["\u4f4d", "<KEYW>,<CJK>"], [":", "<POS>"], ["MySQLDBA", "<ENG>,<TIL>"]], "tags": ["O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 763.8310602066365, 114.47747039794922, 777.4349115249959], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 763.8310602066365, 450.36492919921875, 777.4349115249959], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u5de5", "<CJK>"], ["\u4f5c", "<CJK>"], ["\u804c", "<CJK>"], ["\u8d23", "<CJK>"], [":", "<POS>"], ["MySQL", "<ENG>"], ["\u7ba1", "<CJK>"], ["\u7406", "<CJK>"], [",", "<POS>"], ["\u6027", "<CJK>,<TIL>"], ["\u80fd", "<CJK>,<TIL>"], ["\u4f18", "<CJK>,<TIL>"], ["\u5316", "<CJK>,<TIL>"], [",", "<POS>"], ["\u6570", "<CJK>,<TIL>"], ["\u636e", "<CJK>,<TIL>"], ["\u5e93", "<CJK>,<TIL>"], ["\u8bbe", "<CJK>,<TIL>"], ["\u8ba1", "<CJK>,<TIL>"], [";", "<POS>"], ["\u670d", "<CJK>"], ["\u52a1", "<CJK>"], ["\u5668", "<CJK>"], ["\u7ba1", "<CJK>"], ["\u7406", "<CJK>"], [",", "<POS>"], ["\u5b89", "<CJK>"], ["\u5168", "<CJK>"], [";", "<POS>"], ["\u5b58", "<CJK>"], ["\u50a8", "<CJK>"], ["\u8bbe", "<CJK>"], ["\u5907", "<CJK>"], ["\u7ba1", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 781.5723169205037, 142.08465576171875, 795.176168238863], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u7406", "<CJK>"], ["\u7b49", "<CJK>"]], "tags": ["O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 799.3135888931599, 114.47747039794922, 812.9174402115193], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 799.3135888931599, 169.69186401367188, 812.9174402115193], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u5de5", "<KEYW>,<CJK>"], ["\u4f5c", "<KEYW>,<CJK>"], ["\u5185", "<KEYW>,<CJK>"], ["\u5bb9", "<KEYW>,<CJK>"], [":", "<POS>"]], "tags": ["O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 817.0548608658162, 454.96612548828125, 830.6587121841756], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["1", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u8d1f", "<KEYW>,<CJK>"], ["\u8d23", "<KEYW>,<CJK>"], ["\u5e7f", "<CJK>,<COM>"], ["\u5dde", "<CJK>,<COM>"], ["\u79fb", "<CJK>,<COM>"], ["\u52a8", "<CJK>,<COM>"], ["APP", "<ENG>"], [",", "<POS>"], ["\u4e1a", "<CJK>"], ["\u52a1", "<CJK>"], ["\u914d", "<CJK>"], ["\u7f6e", "<CJK>"], ["\u5e73", "<CJK>"], ["\u53f0", "<CJK>"], ["\u7b49", "<CJK>"], ["\u591a", "<CJK>"], ["\u4e2a", "<CJK>"], ["\u4e1a", "<CJK>"], ["\u52a1", "<CJK>"], [",", "<POS>"], ["30", "<NUM>"], ["\u591a", "<CJK>"], ["\u53f0", "<CJK>"], ["MySQLDB", "<ENG>"], ["\u670d", "<CJK>,<TIL>"], ["\u52a1", "<CJK>,<TIL>"], ["\u5668", "<CJK>,<TIL>"], ["\u8fd0", "<CJK>,<TIL>"], ["\u7ef4", "<CJK>,<TIL>"], [",", "<POS>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 834.7961328384724, 450.36492919921875, 848.3999841568318], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u5305", "<CJK>"], ["\u62ec", "<CJK>"], ["\u65e5", "<CJK>,<TIL>"], ["\u5e38", "<CJK>,<TIL>"], ["\u7ba1", "<CJK>,<TIL>"], ["\u7406", "<CJK>,<TIL>"], [",", "<POS>"], ["\u6027", "<CJK>"], ["\u80fd", "<CJK>"], ["\u8c03", "<CJK>"], ["\u4f18", "<CJK>"], [",", "<POS>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u5927", "<CJK>"], ["\u91cf", "<CJK>"], ["\u65e5", "<CJK>"], ["\u5e38", "<CJK>"], ["\u5de5", "<CJK>"], ["\u4f5c", "<CJK>"], ["\u81ea", "<CJK>"], ["\u52a8", "<CJK>"], ["\u5316", "<CJK>"], [",", "<POS>"], ["\u7cfb", "<CJK>,<TIL>"], ["\u7edf", "<CJK>,<TIL>"], ["\u76d1", "<CJK>,<TIL>"], ["\u63a7", "<CJK>,<TIL>"], ["\u7b49", "<CJK>"], [";", "<POS>"], ["\u5e76", "<CJK>"], ["\u5236", "<CJK>"], ["\u5b9a", "<CJK>"], ["\u76f8", "<CJK>"], ["\u5173", "<CJK>"], ["\u5de5", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 852.5374048111287, 188.09664916992188, 866.141256129488], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u4f5c", "<CJK>"], ["\u6d41", "<CJK>"], ["\u7a0b", "<CJK>"], ["\u89c4", "<CJK>"], ["\u8303", "<CJK>"], ["\u6587", "<CJK>"], ["\u6863", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [142.092041015625, 868.3074243423787, 448.8427429199219, 881.911275660738], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["2", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u6df1", "<CJK>,<LOC>"], ["\u5733", "<CJK>,<LOC>"], ["\u548c", "<CJK>"], ["\u4f5b", "<CJK>,<LOC>"], ["\u5c71", "<CJK>,<LOC>"], ["\u7684", "<CJK>"], ["TT", "<ENG>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"], ["600", "<NUM>"], ["G", "<ENG>"], ["\u7684", "<CJK>"], ["\u6570", "<CJK>,<TIL>"], ["\u636e", "<CJK>,<TIL>"], ["\u8fc1", "<CJK>,<TIL>"], ["\u79fb", "<CJK>,<TIL>"], ["\u5230", "<CJK>"], ["mysql", "<ENG>"], [",", "<POS>"], ["\u4f7f", "<CJK>"], ["\u7528", "<CJK>"], ["keepalived", "<ENG>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 882.1061914322224, 206.50143432617188, 895.7100427505818], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["mysql", "<ENG>"], ["\u7684", "<CJK>"], ["\u9ad8", "<CJK>"], ["\u53ef", "<CJK>"], ["\u7528", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [142.092041015625, 895.9049585220662, 450.36492919921875, 909.5088098404256], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["3", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u5bf9", "<CJK>"], ["\u7ebf", "<CJK>"], ["\u4e0a", "<CJK>"], ["30", "<NUM>"], ["\u53f0", "<CJK>"], ["mysql", "<ENG>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"], ["\u8fdb", "<CJK>"], ["\u884c", "<CJK>"], ["\u7248", "<CJK>"], ["\u672c", "<CJK>"], ["\u5347", "<CJK>"], ["\u7ea7", "<CJK>"], [",", "<POS>"], ["\u4ee5", "<CJK>"], ["\u53ca", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u76ee", "<CJK>"], ["\u5f55", "<CJK>"], ["\u548c", "<CJK>"], ["\u65e5", "<CJK>"], ["\u5fd7", "<CJK>"], ["\u76ee", "<CJK>"], ["\u5f55", "<CJK>"], ["\u7684", "<CJK>"], ["\u6269", "<CJK>"], ["\u5bb9", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [142.092041015625, 909.0466516373006, 358.33966064453125, 922.6505029556599], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["4", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["oralcecrm", "<ENG>"], ["\u5e93", "<CJK>"], ["600", "<NUM>"], ["G", "<ENG>"], ["\u7684", "<CJK>"], ["\u6570", "<CJK>,<TIL>"], ["\u636e", "<CJK>,<TIL>"], ["\u8fc1", "<CJK>,<TIL>"], ["\u79fb", "<CJK>,<TIL>"], ["\u5230", "<CJK>"], ["postgresql", "<ENG>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [142.092041015625, 922.8453882095662, 450.36492919921875, 936.4492395279256], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["5", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["oracle", "<ENG>,<TIL>"], ["\u5386", "<CJK>"], ["\u53f2", "<CJK>"], ["\u6570", "<CJK>,<DPT>"], ["\u636e", "<CJK>,<DPT>"], ["\u4e2d", "<CJK>,<DPT>"], ["\u5fc3", "<CJK>,<DPT>"], ["1", "<NUM>"], ["T", "<ENG>"], ["\u7684", "<CJK>"], ["\u6570", "<CJK>,<TIL>"], ["\u636e", "<CJK>,<TIL>"], ["\u8fc1", "<CJK>,<TIL>"], ["\u79fb", "<CJK>,<TIL>"], ["\u5230", "<CJK>"], ["mysql", "<ENG>"], [",", "<POS>"], ["\u5e76", "<CJK>"], ["\u4f7f", "<CJK>"], ["\u7528", "<CJK>"], ["mycat", "<ENG>"], ["\u8fdb", "<CJK>"], ["\u884c", "<CJK>"], ["\u6c34", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [160.49685668945312, 936.6441552994099, 344.537353515625, 950.2480066177693], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 1, "text": [["\u5e73", "<CJK>"], ["\u5206", "<CJK>"], ["\u5e93", "<CJK>"], [",", "<POS>"], ["\u4e14", "<CJK>"], ["\u4fdd", "<CJK>"], ["\u8bc1", "<CJK>"], ["\u6bcf", "<CJK>"], ["\u4e2a", "<CJK>"], ["\u8282", "<CJK>"], ["\u70b9", "<CJK>"], ["\u7684", "<CJK>"], ["mysql", "<ENG>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u9ad8", "<CJK>"], ["\u53ef", "<CJK>"], ["\u7528", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [90.82156372070312, 977.8239648697224, 429.4896240234375, 993.3807275650349], "fsize": 10.513161659240723, "font": "NotoSansCJKsc-Bold", "color": [0, 0, 0], "bidx": 5, "page": 1, "text": [["2015", "<NUM>,<TMR>,<TMS>"], ["/", "<POS>,<TMR>"], ["3", "<TMR>,<NUM>"], ["-", "<POS>,<TMR>"], ["2017", "<NUM>,<TMR>,<TMS>"], ["/", "<POS>,<TMR>"], ["5", "<TMR>,<NUM>"], [":", "<POS>"], ["\u9752", "<CJK>,<LOC>"], ["\u5c9b", "<CJK>,<LOC>"], ["\u767e", "<CJK>,<CNUM>"], ["\u6d0b", "<CJK>"], ["\u5065", "<CJK>"], ["\u5eb7", "<CJK>"], ["\u836f", "<CJK>"], ["\u623f", "<CJK>"], ["\u8fde", "<CJK>"], ["\u9501", "<CJK>"], ["\u6709", "<KEYW>,<CJK>"], ["\u9650", "<KEYW>,<CJK>"], ["\u516c", "<KEYW>,<CJK>"], ["\u53f8", "<KEYW>,<CJK>"], ["\u5e7f", "<CJK>,<TIL>"], ["\u5dde", "<CJK>,<TIL>"], ["\u5206", "<CJK>,<TIL>"], ["\u516c", "<CJK>,<TIL>"], ["\u53f8", "<CJK>,<TIL>"], ["|", "<POS>"], ["MySQL", "<ENG>"]], "tags": ["B-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "O", "B-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company", "O", "O"], "cats": "Work,Work"}], [{"pos": [90.82156372070312, 990.9656579849568, 112.67990112304688, 1006.5224206802693], "fsize": 10.513161659240723, "font": "NotoSansCJKsc-Bold", "color": [0, 0, 0], "bidx": 5, "page": 1, "text": [["DBA", "<ENG>,<TIL>"]], "tags": ["O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1020.0938623306599, 114.47747039794922, 1033.6977136490193], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1020.0938623306599, 197.29904174804688, 1033.6977136490193], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u6240", "<CJK>,<TIL>"], ["\u5c5e", "<CJK>,<TIL>"], ["\u884c", "<CJK>,<TIL>"], ["\u4e1a", "<CJK>,<TIL>"], [":", "<POS>"], ["\u4e92", "<CJK>"], ["\u8054", "<CJK>"], ["\u7f51", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1038.4922693130818, 114.47747039794922, 1052.096090113863], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1038.4922693130818, 212.09017944335938, 1052.096090113863], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u5de5", "<KEYW>,<CJK>"], ["\u4f5c", "<KEYW>,<CJK>"], ["\u5c97", "<KEYW>,<CJK>"], ["\u4f4d", "<KEYW>,<CJK>"], [":", "<POS>"], ["MySQLDBA", "<ENG>,<TIL>"]], "tags": ["O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1056.233541285738, 114.47747039794922, 1069.8373620865193], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1056.233541285738, 450.36492919921875, 1069.8373620865193], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u5de5", "<CJK>"], ["\u4f5c", "<CJK>"], ["\u804c", "<CJK>"], ["\u8d23", "<CJK>"], [":", "<POS>"], ["MySQL", "<ENG>"], ["\u7ba1", "<CJK>"], ["\u7406", "<CJK>"], [",", "<POS>"], ["\u6027", "<CJK>,<TIL>"], ["\u80fd", "<CJK>,<TIL>"], ["\u4f18", "<CJK>,<TIL>"], ["\u5316", "<CJK>,<TIL>"], [",", "<POS>"], ["\u6570", "<CJK>,<TIL>"], ["\u636e", "<CJK>,<TIL>"], ["\u5e93", "<CJK>,<TIL>"], ["\u8bbe", "<CJK>,<TIL>"], ["\u8ba1", "<CJK>,<TIL>"], [";", "<POS>"], ["\u670d", "<CJK>"], ["\u52a1", "<CJK>"], ["\u5668", "<CJK>"], ["\u7ba1", "<CJK>"], ["\u7406", "<CJK>"], [",", "<POS>"], ["\u5b89", "<CJK>"], ["\u5168", "<CJK>"], [";", "<POS>"], ["\u5b58", "<CJK>"], ["\u50a8", "<CJK>"], ["\u8bbe", "<CJK>"], ["\u5907", "<CJK>"], ["\u7ba1", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1073.9748132583943, 142.08465576171875, 1087.5786340591756], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u7406", "<CJK>"], ["\u7b49", "<CJK>"]], "tags": ["O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1091.7160852310506, 114.47747039794922, 1105.3199060318318], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1091.7160852310506, 169.69186401367188, 1105.3199060318318], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u5de5", "<KEYW>,<CJK>"], ["\u4f5c", "<KEYW>,<CJK>"], ["\u5185", "<KEYW>,<CJK>"], ["\u5bb9", "<KEYW>,<CJK>"], [":", "<POS>"]], "tags": ["O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [142.092041015625, 1109.4573572037068, 154.12542905129942, 1123.061178004488], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["1", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"]], "tags": ["O", "O"], "cats": "Work,Work"}, {"pos": [160.49685668945312, 1109.4573572037068, 450.36492919921875, 1123.061178004488], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u90e8", "<CJK>"], ["\u7f72", "<CJK>"], ["MySQL", "<ENG>"], ["\u67b6", "<CJK>"], ["\u6784", "<CJK>"], [",", "<POS>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u57fa", "<CJK>"], ["\u4e8e", "<CJK>"], ["keepalived", "<ENG>"], ["+", "<POS>"], ["GTID", "<ENG>"], ["\u7684", "<CJK>"], ["\u4e3b", "<CJK>"], ["\u4ece", "<CJK>"], ["\u590d", "<CJK>"], ["\u5236", "<CJK>"], [",", "<POS>"], ["\u4e3b", "<CJK>"], ["\u4e3b", "<CJK>"], ["\u590d", "<CJK>"], ["\u5236", "<CJK>"], ["\u548c", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1127.198629176363, 291.2949523925781, 1140.8024499771443], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["MHA", "<ENG>"], ["\u7684", "<CJK>"], ["\u9ad8", "<CJK>"], ["\u53ef", "<CJK>"], ["\u7528", "<CJK>"], [",", "<POS>"], ["\u4ee5", "<CJK>"], ["\u53ca", "<CJK>"], ["\u8bfb", "<CJK>"], ["\u5199", "<CJK>"], ["\u5206", "<CJK>"], ["\u79bb", "<CJK>"], ["\u548c", "<CJK>"], ["\u8d1f", "<CJK>"], ["\u8f7d", "<CJK>"], ["\u5747", "<CJK>"], ["\u8861", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [142.092041015625, 1144.9399011490193, 153.6626064345427, 1158.5437219498006], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["2", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"]], "tags": ["O", "O"], "cats": "Work,Work"}, {"pos": [160.49685668945312, 1144.9399011490193, 450.36492919921875, 1158.5437219498006], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u5236", "<CJK>"], ["\u5b9a", "<CJK>"], ["\u5907", "<CJK>"], ["\u4efd", "<CJK>"], ["\u7b56", "<CJK>"], ["\u7565", "<CJK>"], [",", "<POS>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u57fa", "<CJK>"], ["\u4e8e", "<CJK>"], ["xtrabackup", "<ENG>"], ["+", "<POS>"], ["binlog", "<ENG>"], ["\u5168", "<CJK>"], ["\u91cf", "<CJK>"], ["\u53ca", "<CJK>"], ["\u589e", "<CJK>"], ["\u91cf", "<CJK>"], ["\u5907", "<CJK>"], ["\u4efd", "<CJK>"], ["\u548c", "<CJK>"], ["\u57fa", "<CJK>"], ["\u4e8e", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1162.6811731216756, 277.4913635253906, 1176.2849939224568], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["mysqldump", "<ENG>"], ["+", "<POS>"], ["binglog", "<ENG>"], ["\u7684", "<CJK>"], ["\u5168", "<CJK>"], ["\u91cf", "<CJK>"], ["\u53ca", "<CJK>"], ["\u589e", "<CJK>"], ["\u91cf", "<CJK>"], ["\u5907", "<CJK>"], ["\u4efd", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1180.4224450943318, 135.2578212782927, 1194.026265895113], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["3", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"]], "tags": ["O", "O"], "cats": "Work,Work"}, {"pos": [142.092041015625, 1180.4224450943318, 450.36492919921875, 1194.026265895113], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 6, "page": 1, "text": [["\u6062", "<CJK>"], ["\u590d", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], [",", "<POS>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u57fa", "<CJK>"], ["\u4e8e", "<CJK>"], ["mysqlbinlog", "<ENG>"], ["_", "<POS>"], ["flashback", "<ENG>"], ["\u548c", "<CJK>"], ["binlog", "<ENG>"], ["2", "<NUM>"], ["sql", "<ENG>"], ["\u7684", "<CJK>"], ["\u95ea", "<CJK>"], ["\u56de", "<CJK>"], [",", "<POS>"], ["\u5c06", "<CJK>"], ["\u7ebf", "<CJK>"], ["\u4e0a", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1207.8904925118666, 372.1445617675781, 1221.4943285714369], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["\u7684", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u6062", "<CJK>"], ["\u590d", "<CJK>"], ["\u5230", "<CJK>"], ["\u6545", "<CJK>"], ["\u969c", "<CJK>"], ["\u524d", "<CJK>"], ["\u4ee5", "<CJK>"], ["\u53ca", "<CJK>"], ["\u6839", "<CJK>"], ["\u636e", "<CJK>"], ["\u5907", "<CJK>"], ["\u4efd", "<CJK>"], ["\u6062", "<CJK>"], ["\u590d", "<CJK>"], ["\u7ebf", "<CJK>"], ["\u4e0b", "<CJK>"], ["\u6d4b", "<CJK>"], ["\u8bd5", "<CJK>"], ["\u73af", "<CJK>"], ["\u5883", "<CJK>"], ["\u7684", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1225.6317644845228, 135.2578212782927, 1239.2356005440931], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["4", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"]], "tags": ["O", "O"], "cats": "Work,Work"}, {"pos": [142.092041015625, 1225.6317644845228, 450.36492919921875, 1239.2356005440931], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["\u5bf9", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"], ["\u8c03", "<CJK>"], ["\u4f18", "<CJK>"], [",", "<POS>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u64cd", "<CJK>"], ["\u4f5c", "<CJK>"], ["\u7cfb", "<CJK>"], ["\u7edf", "<CJK>"], ["\u7684", "<CJK>"], ["\u8c03", "<CJK>"], ["\u4f18", "<CJK>"], [",", "<POS>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"], ["\u53c2", "<CJK>"], ["\u6570", "<CJK>"], ["\u7684", "<CJK>"], ["\u8c03", "<CJK>"], ["\u4f18", "<CJK>"], [",", "<POS>"], ["\u8868", "<CJK>"], ["\u7ed3", "<CJK>"], ["\u6784", "<CJK>"], ["\u7684", "<CJK>"], ["\u8c03", "<CJK>"], ["\u4f18", "<CJK>"], ["\u4ee5", "<CJK>"], ["\u53ca", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1243.3730288277845, 286.6937255859375, 1256.9768648873548], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["SQL", "<ENG>"], ["\u53ca", "<CJK>"], ["\u7d22", "<CJK>"], ["\u5f15", "<CJK>"], ["\u8c03", "<CJK>"], ["\u4f18", "<CJK>"], [",", "<POS>"], ["\u63d0", "<CJK>"], ["\u9ad8", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"], ["\u7684", "<CJK>"], ["\u8fd0", "<CJK>"], ["\u884c", "<CJK>"], ["\u6548", "<CJK>"], ["\u7387", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1261.1143160592298, 450.36492919921875, 1274.7181597481947], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["5", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"], ["\u76d1", "<CJK>"], ["\u63a7", "<CJK>"], [",", "<POS>"], ["\u914d", "<CJK>"], ["\u7f6e", "<CJK>"], ["ZABBIX", "<ENG>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u5b9e", "<CJK>"], ["\u65f6", "<CJK>"], ["\u7684", "<CJK>"], ["\u5bf9", "<CJK>"], ["MySQL", "<ENG>"], ["\u7684", "<CJK>"], ["qps", "<ENG>"], ["/", "<POS>"], ["tps", "<ENG>"], ["/", "<POS>"], ["\u4e3b", "<CJK>"], ["\u4ece", "<CJK>"], ["\u72b6", "<CJK>"], ["\u6001", "<CJK>"], ["/", "<POS>"], ["\u9501", "<CJK>"], ["\u7b49", "<CJK>"], ["\u5404", "<CJK>"], ["\u65b9", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1278.8555804024916, 243.31100463867188, 1292.459431720851], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["\u9762", "<CJK>"], [",", "<POS>"], ["\u4fdd", "<CJK>"], ["\u8bc1", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u7a33", "<CJK>"], ["\u5b9a", "<CJK>"], ["\u9ad8", "<CJK>"], ["\u6548", "<CJK>"], ["\u7684", "<CJK>"], ["\u8fd0", "<CJK>"], ["\u884c", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1297.2539263497572, 450.36492919921875, 1310.8577776681166], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["6", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u5728", "<CJK>"], ["\u7ebf", "<CJK>"], ["\u4fee", "<CJK>"], ["\u6539", "<CJK>"], ["\u8868", "<CJK>"], ["\u7ed3", "<CJK>"], ["\u6784", "<CJK>"], ["\u548c", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], [",", "<POS>"], ["\u4f7f", "<CJK>"], ["\u7528", "<CJK>"], ["PT", "<ENG>"], ["-", "<POS>"], ["OSC", "<ENG>"], ["\u548c", "<CJK>"], ["inception", "<ENG>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u5728", "<CJK>"], ["\u7ebf", "<CJK>"], ["\u5bf9", "<CJK>"], ["\u5927", "<CJK>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u7684", "<CJK>"], ["\u8868", "<CJK>"], ["\u8fdb", "<CJK>"], ["\u884c", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1314.9951983224134, 187.78818828017916, 1328.5990496407728], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["DDL", "<ENG>"], ["\u548c", "<CJK>"], ["DML", "<ENG>"]], "tags": ["O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1332.7364855538588, 349.1385803222656, 1346.3403368722181], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["7", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u90e8", "<CJK>"], ["\u7f72", "<CJK>"], ["mongodb", "<ENG>"], ["\u590d", "<CJK>"], ["\u5236", "<CJK>"], ["\u96c6", "<CJK>"], ["\u548c", "<CJK>"], ["redis", "<ENG>"], ["\u96c6", "<CJK>"], ["\u7fa4", "<CJK>"], [",", "<POS>"], ["\u7ef4", "<CJK>"], ["\u62a4", "<CJK>"], ["\u96c6", "<CJK>"], ["\u7fa4", "<CJK>"], ["\u7684", "<CJK>"], ["\u7a33", "<CJK>"], ["\u5b9a", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1350.477757526515, 358.3409423828125, 1364.0816088448744], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 1, "page": 2, "colum": 2, "text": [["8", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u7f16", "<CJK>"], ["\u5199", "<CJK>"], ["shell", "<ENG>,<TIL>"], ["\u811a", "<CJK>"], ["\u672c", "<CJK>"], [",", "<POS>"], ["\u5b9a", "<CJK>"], ["\u671f", "<CJK>"], ["\u5bf9", "<CJK>"], ["MySQL", "<ENG>"], ["\u6570", "<CJK>"], ["\u636e", "<CJK>"], ["\u5e93", "<CJK>"], ["\u8fdb", "<CJK>"], ["\u884c", "<CJK>"], ["\u5de1", "<CJK>"], ["\u68c0", "<CJK>"], ["\u548c", "<CJK>"], ["\u8fd0", "<CJK>"], ["\u7ef4", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [90.82156372070312, 1389.0292254220228, 307.24481201171875, 1404.5859728585463], "fsize": 10.513161659240723, "font": "NotoSansCJKsc-Bold", "color": [0, 0, 0], "bidx": 2, "page": 2, "colum": 2, "text": [["2013", "<NUM>,<TMR>,<TMS>"], ["/", "<POS>,<TMR>"], ["6", "<TMR>,<NUM>"], ["-", "<POS>,<TMR>"], ["2015", "<NUM>,<TMR>,<TMS>"], ["/", "<POS>,<TMR>"], ["2", "<TMR>,<NUM>"], [":", "<POS>"], ["\u5357", "<CJK>,<COM>"], ["\u65b9", "<CJK>,<COM>"], ["\u90fd", "<CJK>,<COM>"], ["\u5e02", "<CJK>,<COM>"], ["\u62a5", "<CJK>,<COM>"], ["|", "<POS>"], ["MySQLDBA", "<ENG>,<TIL>"]], "tags": ["B-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "I-timeRange", "O", "B-company", "I-company", "I-company", "I-company", "I-company", "I-company", "I-company"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1418.1574145089369, 114.47747039794922, 1431.7612658272963], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1418.1574145089369, 188.09664916992188, 1431.7612658272963], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 2, "text": [["\u6240", "<CJK>,<TIL>"], ["\u5c5e", "<CJK>,<TIL>"], ["\u884c", "<CJK>,<TIL>"], ["\u4e1a", "<CJK>,<TIL>"], [":", "<POS>"], ["\u4f20", "<CJK>"], ["\u5a92", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1435.8986864815931, 114.47747039794922, 1449.5025377999525], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1435.8986864815931, 215.70382690429688, 1449.5025377999525], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 2, "text": [["\u5de5", "<KEYW>,<CJK>"], ["\u4f5c", "<KEYW>,<CJK>"], ["\u5c97", "<KEYW>,<CJK>"], ["\u4f4d", "<KEYW>,<CJK>"], [":", "<POS>"], ["\u8fd0", "<CJK>,<TIL>"], ["\u7ef4", "<CJK>,<TIL>"], ["\u5de5", "<CJK>,<TIL>"], ["\u7a0b", "<CJK>,<TIL>"], ["\u5e08", "<CJK>,<TIL>"]], "tags": ["O", "O", "O", "O", "O", "B-title", "I-title", "I-title", "I-title", "I-title"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1453.6399584542494, 114.47747039794922, 1467.2438097726088], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1453.6399584542494, 450.36492919921875, 1467.2438097726088], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 2, "text": [["\u5de5", "<CJK>"], ["\u4f5c", "<CJK>"], ["\u804c", "<CJK>"], ["\u8d23", "<CJK>"], [":", "<POS>"], ["LNMP", "<ENG>"], ["\u67b6", "<CJK>"], ["\u6784", "<CJK>"], ["\u7ef4", "<CJK>"], ["\u62a4", "<CJK>"], [";", "<POS>"], ["MySQL", "<ENG>"], ["\u7ba1", "<CJK>"], ["\u7406", "<CJK>"], [",", "<POS>"], ["\u6027", "<CJK>,<TIL>"], ["\u80fd", "<CJK>,<TIL>"], ["\u4f18", "<CJK>,<TIL>"], ["\u5316", "<CJK>,<TIL>"], [",", "<POS>"], ["\u6570", "<CJK>,<TIL>"], ["\u636e", "<CJK>,<TIL>"], ["\u5e93", "<CJK>,<TIL>"], ["\u8bbe", "<CJK>,<TIL>"], ["\u8ba1", "<CJK>,<TIL>"], [";", "<POS>"], ["\u670d", "<CJK>"], ["\u52a1", "<CJK>"], ["\u5668", "<CJK>"], ["\u7ba1", "<CJK>"], ["\u7406", "<CJK>"], [",", "<POS>"], ["\u5b89", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1471.3812304269056, 206.50143432617188, 1484.985081745265], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 2, "text": [["\u5168", "<CJK>"], [";", "<POS>"], ["\u5b58", "<CJK>"], ["\u50a8", "<CJK>"], ["\u8bbe", "<CJK>,<TIL>"], ["\u5907", "<CJK>,<TIL>"], ["\u7ba1", "<CJK>,<TIL>"], ["\u7406", "<CJK>,<TIL>"], ["\u7b49", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [105.282470703125, 1489.12253291714, 114.47747039794922, 1502.7263842354994], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 1, "text": [["\ufffd", "<POS>"]], "tags": ["O"], "cats": "Work,Work"}, {"pos": [123.687255859375, 1489.12253291714, 169.69186401367188, 1502.7263842354994], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 3, "page": 2, "colum": 2, "text": [["\u5de5", "<KEYW>,<CJK>"], ["\u4f5c", "<KEYW>,<CJK>"], ["\u5185", "<KEYW>,<CJK>"], ["\u5bb9", "<KEYW>,<CJK>"], [":", "<POS>"]], "tags": ["O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1518.6913195382338, 404.3529357910156, 1532.2951708565931], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 2, "colum": 2, "text": [["1", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u90e8", "<CJK>"], ["\u7f72", "<CJK>"], ["LNMP", "<ENG>"], ["\u67b6", "<CJK>"], ["\u6784", "<CJK>"], [",", "<POS>"], ["\u4f7f", "<CJK>"], ["\u7528", "<CJK>"], ["LVS", "<ENG>"], ["+", "<POS>"], ["KEEPALIVED", "<ENG>"], ["\u642d", "<CJK>"], ["\u5efa", "<CJK>"], ["\u9ad8", "<CJK>"], ["\u53ef", "<CJK>"], ["\u7528", "<CJK>"], ["\u6027", "<CJK>"], ["\u8d1f", "<CJK>"], ["\u8f7d", "<CJK>"], ["\u5747", "<CJK>"], ["\u8861", "<CJK>"], ["\u96c6", "<CJK>"], ["\u7fa4", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1532.4900866280775, 450.36492919921875, 1546.0939379464369], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 2, "colum": 2, "text": [["2", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u5728", "<CJK>"], ["\u56db", "<CJK>,<CNUM>"], ["\u5c42", "<CJK>"], ["\u5206", "<CJK>"], ["\u53d1", "<CJK>"], ["\u7684", "<CJK>"], ["\u90fd", "<CJK>"], ["\u540e", "<CJK>"], ["\u7aef", "<CJK>"], [",", "<POS>"], ["\u4f7f", "<CJK>"], ["\u7528", "<CJK>"], ["haproxy", "<ENG>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u5bf9", "<CJK>"], ["es", "<ENG>"], ["\u7684", "<CJK>"], ["\u4e03", "<CJK>,<CNUM>"], ["\u5c42", "<CJK>"], ["\u8c03", "<CJK>"], ["\u5ea6", "<CJK>"], [",", "<POS>"], ["\u5b9e", "<CJK>"], ["\u73b0", "<CJK>"], ["\u641c", "<CJK>"], ["\u7d22", "<CJK>"], ["\u670d", "<CJK>"], ["\u52a1", "<CJK>"], ["\u5668", "<CJK>"], ["\u7684", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [86.87767791748047, 1546.2888537179213, 123.67987060546875, 1559.8927050362806], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 2, "colum": 1, "text": [["\u8d1f", "<CJK>"], ["\u8f7d", "<CJK>"], ["\u5747", "<CJK>"], ["\u8861", "<CJK>"]], "tags": ["O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1559.4305468331556, 390.5493469238281, 1573.034398151515], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 2, "colum": 2, "text": [["3", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u8fd0", "<CJK>"], ["\u7528", "<CJK>"], ["iptables", "<ENG>"], ["\u5bf9", "<CJK>"], ["\u7f51", "<CJK>"], ["\u7edc", "<CJK>"], ["\u8fdb", "<CJK>"], ["\u884c", "<CJK>"], ["\u5b89", "<CJK>"], ["\u5168", "<CJK>"], ["\u9694", "<CJK>,<LOC>"], ["\u79bb", "<CJK>,<LOC>"], [",", "<POS>"], ["\u9632", "<CJK>"], ["\u5fa1", "<CJK>"], ["\u516c", "<CJK>"], ["\u7f51", "<CJK>"], ["\u4ea7", "<CJK>"], ["\u751f", "<CJK>"], ["\u7684", "<CJK>"], ["\u5404", "<CJK>"], ["\u7c7b", "<CJK>"], ["\u653b", "<CJK>"], ["\u51fb", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1573.2292834054213, 374.11651611328125, 1586.8331347237806], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 2, "colum": 2, "text": [["4", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u642d", "<CJK>"], ["\u5efa", "<CJK>"], ["\u76d1", "<CJK>"], ["\u63a7", "<CJK>"], ["\u5e73", "<CJK>"], ["\u53f0", "<CJK>"], ["nagios", "<ENG>"], ["\u548c", "<CJK>"], ["zabbix", "<ENG>"], [",", "<POS>"], ["\u5e76", "<CJK>"], ["\u4e14", "<CJK>"], ["\u8d1f", "<KEYW>,<CJK>"], ["\u8d23", "<KEYW>,<CJK>"], ["\u540e", "<CJK>"], ["\u671f", "<CJK>"], ["\u7684", "<CJK>"], ["\u7ef4", "<CJK>"], ["\u62a4", "<CJK>"], ["\u76d1", "<CJK>"], ["\u63a7", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}], [{"pos": [123.687255859375, 1587.028050495265, 364.9140930175781, 1600.6319018136244], "fsize": 9.193392753601074, "font": "NotoSansCJKsc-Regular", "color": [0, 0, 0], "bidx": 4, "page": 2, "colum": 2, "text": [["5", "<NUM>,<ORDER>"], [".", "<POS>,<ORDER>"], ["\u642d", "<CJK>"], ["\u5efa", "<CJK>"], ["\u5e38", "<CJK>"], ["\u7528", "<CJK>"], ["\u7684", "<CJK>"], ["\u57fa", "<CJK>,<TIL>"], ["\u7840", "<CJK>,<TIL>"], ["\u670d", "<CJK>,<TIL>"], ["\u52a1", "<CJK>,<TIL>"], ["vsftp", "<ENG>"], [",", "<POS>"], ["Samba", "<ENG>"], [",", "<POS>"], ["nfs", "<ENG>"], [",", "<POS>"], ["\u63d0", "<CJK>"], ["\u9ad8", "<CJK>"], ["\u5de5", "<CJK>"], ["\u4f5c", "<CJK>"], ["\u6548", "<CJK>"], ["\u7387", "<CJK>"]], "tags": ["O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O", "O"], "cats": "Work,Work"}]]}

In [6]:
block = Block.from_dict(data)
block

Block([Line([Span(pos=Position(left=86.87767791748047, top=668.3373620865193, right=97.3926773071289, down=683.8941095230427), fsize=10.513161659240723, font='NotoSansCJKsc-Regular', color=Color(r=0, g=0, b=0), tokens=['�'], token_tags=['<POS>'], text='�', tag=''),
             Span(pos=Position(left=105.282470703125, top=668.3373620865193, right=145.37660217285156, down=683.8941095230427), fsize=10.513161659240723, font='NotoSansCJKsc-Bold', color=Color(r=0, g=0, b=0), tokens=['工', '作', '经', '历'], token_tags=['<KEYW>,<CJK>', '<KEYW>,<CJK>', '<KEYW>,<CJK>', '<KEYW>,<CJK>'], text='工作经历', tag='')]),
       Line([Span(pos=Position(left=90.82156372070312, top=699.2203119156209, right=131.38987731933594, down=714.7770593521443), fsize=10.513161659240723, font='NotoSansCJKsc-Bold', color=Color(r=0, g=0, b=0), tokens=['2017', '/', '5', '-'], token_tags=['<NUM>,<TMR>,<TMS>', '<POS>,<TMR>', '<TMR>,<NUM>', '<POS>,<TMR>'], text='2017/5-', tag='timeRange'),
             Span(pos=Position(left=141.

In [9]:
record = BlockHandcraftRecord.from_block(block)

record

BlockHandcraftRecord(span_features=[{'line_id': '0', 'line_leading_fsize': 10.513161659240723, 'line_max_fsize': 10.513161659240723, 'line_is_same_fsize': True, 'line_is_same_fsize_with_prev': True, 'line_is_same_fsize_with_next': True, 'line_is_same_font': False, 'line_is_same_color': True, 'line_num_spans': 2, 'line_left_margin': 0.0, 'line_right_margin': 309.5895233154297, 'line_top_margin': 0, 'line_down_margin': 15.326202392578125, 'line_is_most_left': True, 'line_is_most_right': False, 'line_is_align_with_prev': False, 'line_is_align_with_next': False, 'line_max_width': 40.09413146972656, 'line_max_interspace': 7.889793395996094, 'line_average_width': 25.3045654296875, 'line_average_interspace': 7.889793395996094, 'line_num_tokens': 5, 'line_is_startswith_chinese': False, 'line_have_time_range': False, 'prev_line_id': None, 'prev_line_leading_fsize': None, 'prev_line_max_fsize': None, 'prev_line_is_same_fsize': None, 'prev_line_is_same_fsize_with_prev': None, 'prev_line_is_same_f

In [10]:
records = record.to_flat_records()

records

([{'line_id': True,
   'line_leading_fsize': 0.0,
   'line_max_fsize': 0.0,
   'line_is_same_fsize': True,
   'line_is_same_fsize_with_prev': True,
   'line_is_same_fsize_with_next': True,
   'line_is_same_font': True,
   'line_is_same_color': True,
   'line_num_spans': 0,
   'line_left_margin': 0.0,
   'line_right_margin': 0.0,
   'line_top_margin': 0,
   'line_down_margin': 0.0,
   'line_is_most_left': True,
   'line_is_most_right': True,
   'line_is_align_with_prev': True,
   'line_is_align_with_next': True,
   'line_max_width': 0.0,
   'line_max_interspace': 0.0,
   'line_average_width': 0.0,
   'line_average_interspace': 0.0,
   'line_num_tokens': 0,
   'line_is_startswith_chinese': True,
   'line_have_time_range': True,
   'prev_line_id': None,
   'prev_line_leading_fsize': None,
   'prev_line_max_fsize': None,
   'prev_line_is_same_fsize': None,
   'prev_line_is_same_fsize_with_prev': None,
   'prev_line_is_same_fsize_with_next': None,
   'prev_line_is_same_font': None,
   'prev

In [7]:
block = Block.from_dict(source_data[4])
record = BlockHandcraftRecord.from_block(block)

KeyError: 4

In [7]:
records = record.to_flat_records()

{'file': '00000064-318c-4935-ba4d-ec2260992be2.html-zh-cn',
 'objs': [[{'pos': [29.0,
     152.25000762939453,
     91.99977111816406,
     167.79000091552734],
    'fsize': 10.5,
    'font': 'NotoSansCJKsc-Bold',
    'color': [102, 119, 135],
    'bidx': 4,
    'colum': 1,
    'text': [['目', '<CJK>'],
     ['前', '<CJK>'],
     ['职', '<KEYW>,<CJK>'],
     ['位', '<KEYW>,<CJK>'],
     ['概', '<CJK>'],
     ['况', '<CJK>']],
    'tags': ['O', 'O', 'O', 'O', 'O', 'O'],
    'cats': 'Work,Edu'}],
  [{'pos': [83.75, 186.23999786376953, 128.75027465820312, 199.56000518798828],
    'fsize': 9.0,
    'font': 'NotoSansCJKsc-Regular',
    'color': [51, 68, 75],
    'bidx': 5,
    'colum': 1,
    'text': [['公', '<KEYW>,<CJK>'],
     ['司', '<KEYW>,<CJK>'],
     ['名', '<KEYW>,<CJK>'],
     ['称', '<KEYW>,<CJK>'],
     [':', '<POS>']],
    'tags': ['O', 'O', 'O', 'O', 'O'],
    'cats': 'Work,Work'},
   {'pos': [136.25, 186.23999786376953, 208.25048828125, 199.56000518798828],
    'fsize': 9.0,
    'font'

In [21]:
def base_filter(idx, other_idx, tag, other_tag):

    if tag or other_tag:
        return True

    if other_idx - idx <= 2:
        return True
    
    return False